# Investment Strategy

## Import Libraries

In [1]:
# Import Libraries
import numpy as np
import pandas as pd
import hvplot.pandas
from pathlib import Path

In [2]:
# Read CSV into Pandas Dataframe
filepath = Path("../Data/roku_stock_prices_2.csv")
roku_df = pd.read_csv(filepath, parse_dates = True, infer_datetime_format=True)
roku_df.head()

Date   Open   High    Low  Close    Volume
0  5/25/2018 16:00:00  36.06  39.08  35.65  38.54  21203421
1  5/29/2018 16:00:00  39.11  39.88  37.62  38.60  13802296
2  5/30/2018 16:00:00  38.92  39.07  37.31  38.45   7371784
3  5/31/2018 16:00:00  38.20  38.62  37.35  37.46   4160117
4   6/1/2018 16:00:00  37.55  37.81  36.14  37.07   6991263

## Generate a Dual Moving Average Crossover Trading Signal

In [3]:
# Grab just the 'date and 'close' from the dataset
signals_df = roku_df.loc[:, ["Date", "Close"]].copy()

# Set the 'date' column as the index
signals_df = signals_df.set_index("Date", drop=True)

# Set the short window and long window
short_window = 50
long_window = 100

# Generate the short and long moving averages (50 and 100 days, respectively)
signals_df["SMA50"] = signals_df["Close"].rolling(window=short_window).mean()
signals_df["SMA100"] = signals_df["Close"].rolling(window=long_window).mean()

# Initiate the new 'Signal' Column
signals_df["Signal"] = 0.0

# Generate the trading signal of 0 or 1
# where 0 is when the SMA50 is above the SMA100, and
# where 1 is when the SMA50 is below (or crosses over) the SMA100
signals_df["Signal"][short_window:] = np.where(
    signals_df["SMA50"][short_window:] < signals_df["SMA100"][short_window:], 0.0, 1.0
)

# Calculate the points in time ar which the position should be taken, 1 or -1
signals_df["Entry/Exit"] = signals_df["Signal"].diff()

# Print the DataFrame
signals_df.tail()

Close     SMA50    SMA100  Signal  Entry/Exit
Date                                                              
1/14/2021 16:00:00  418.46  303.9844  248.1467     1.0         0.0
1/15/2021 16:00:00  408.30  308.0806  250.7439     1.0         0.0
1/19/2021 16:00:00  434.14  312.4498  253.6076     1.0         0.0
1/20/2021 16:00:00  428.50  316.5186  256.2498     1.0         0.0
1/21/2021 16:00:00  423.64  319.9242  258.8765     1.0         0.0

## Plot Entry and Exit Points of Dual Moving Average Crossover Trading Strategy

In [4]:
# Visualize entry position relative to close price
# Enter or go long when the 50MA crosses above the 100MA
entry = signals_df[signals_df["Entry/Exit"] == 1.0]["Close"].hvplot.scatter(
    color = "green",
    legend = False,
    ylabel = "Price in $",
    width = 1000,
    height = 400
)

# Visualize entry position relative to close price
# Exit or go short when the 50MA crosses below the 100MA
exit = signals_df[signals_df["Entry/Exit"] == -1.0]["Close"].hvplot.scatter(
    color = "red",
    legend = False,
    ylabel = "Price in $",
    width = 1000,
    height = 400
)

# Visualize close price for the investment
security_close = signals_df[["Close"]].hvplot(
    line_color = "lightgray",
    ylabel = "Price in $",
    width = 1000,
    height = 400
)

# Visualize the moving averages
moving_avgs = signals_df[["SMA50", "SMA100"]].hvplot(
    ylabel = "Price in $",
    width = 1000,
    height = 400
)

# Overlay plots
entry_exit_plot = security_close * moving_avgs * entry * exit
entry_exit_plot.opts(xaxis=None)


:Overlay
   .Curve.I          :Curve   [Date]   (Close)
   .NdOverlay.I      :NdOverlay   [Variable]
      :Curve   [Date]   (value)
   .Scatter.Close.I  :Scatter   [Date]   (Close)
   .Scatter.Close.II :Scatter   [Date]   (Close)

### Backtest the Trading Strategy

In [5]:
# Set initial capital
initial_capital = float(10000)

# Set the share size
share_size = 150

# Take a 500 share position where the dual moving avg crossover is 1
signals_df["Position"] = share_size * signals_df["Signal"]

# Find the points in time where a 500 share position is bought or sold
signals_df["Entry/Exit Position"] = signals_df["Position"].diff()

# Multiply share price by entry/exit positions and get the cumulative sum
signals_df["Portfolio Holdings"] = (
    signals_df["Close"] * signals_df["Entry/Exit Position"].cumsum()
)

# Subtract the initial capital by the portfolio holdings to get the liquid cash in the portfolio
signals_df["Portfolio Cash"] = (
    initial_capital -  (signals_df["Close"] * signals_df["Entry/Exit Position"]).cumsum()
)

# Get the total portfolio value by adding the cash amount by the portfolio holdings (or investments)
signals_df["Portfolio Total"] = (
    signals_df["Portfolio Cash"] + signals_df["Portfolio Holdings"]
)

# Calculate the portfolio daily returns
signals_df["Portfolio Daily Returns"] = signals_df["Portfolio Total"].pct_change()

# Calculate the cumulative returns
signals_df["Portfolio Cumulative Returns"] = (
    1 + signals_df["Portfolio Daily Returns"]
).cumprod() - 1

# show df
signals_df.tail()

Close     SMA50    SMA100  Signal  Entry/Exit  Position  \
Date                                                                           
1/14/2021 16:00:00  418.46  303.9844  248.1467     1.0         0.0     150.0   
1/15/2021 16:00:00  408.30  308.0806  250.7439     1.0         0.0     150.0   
1/19/2021 16:00:00  434.14  312.4498  253.6076     1.0         0.0     150.0   
1/20/2021 16:00:00  428.50  316.5186  256.2498     1.0         0.0     150.0   
1/21/2021 16:00:00  423.64  319.9242  258.8765     1.0         0.0     150.0   

                    Entry/Exit Position  Portfolio Holdings  Portfolio Cash  \
Date                                                                          
1/14/2021 16:00:00                  0.0             62769.0           143.5   
1/15/2021 16:00:00                  0.0             61245.0           143.5   
1/19/2021 16:00:00                  0.0             65121.0           143.5   
1/20/2021 16:00:00                  0.0             64275.0           143.5   
1/21/2021 16:00:00                  0.0             63546.0           143.5   

                    Portfolio Total  Portfolio Daily Returns  \
Date                                                           
1/14/2021 16:00:00          62912.5                 0.024075   
1/15/2021 16:00:00          61388.5                -0.024224   
1/19/2021 16:00:00          65264.5                 0.063139   
1/20/2021 16:00:00          64418.5                -0.012963   
1/21/2021 16:00:00          63689.5                -0.011317   

                    Portfolio Cumulative Returns  
Date                                              
1/14/2021 16:00:00                       5.29125  
1/15/2021 16:00:00                       5.13885  
1/19/2021 16:00:00                       5.52645  
1/20/2021 16:00:00                       5.44185  
1/21/2021 16:00:00                       5.36895

## Plot Entry/Exit Points of the Backtest Results

In [6]:
# Visualize entry position relative to total portfolio value
entry = signals_df[signals_df['Entry/Exit'] == 1.0]['Portfolio Total'].hvplot.scatter(
    color='green',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize exit position relative to total portfolio value
exit = signals_df[signals_df['Entry/Exit'] == -1.0]['Portfolio Total'].hvplot.scatter(
    color='red',
    legend=False,
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Visualize total portoflio value for the investment
total_portfolio_value = signals_df[['Portfolio Total']].hvplot(
    line_color='lightblue',
    ylabel='Total Portfolio Value',
    width=1000,
    height=400
)

# Overlay plots
portfolio_entry_exit_plot = total_portfolio_value * entry * exit
portfolio_entry_exit_plot.opts(xaxis=None)

:Overlay
   .Curve.I                    :Curve   [Date]   (Portfolio Total)
   .Scatter.Portfolio_Total.I  :Scatter   [Date]   (Portfolio Total)
   .Scatter.Portfolio_Total.II :Scatter   [Date]   (Portfolio Total)

## Prepare Portfolio Evaluation Metrics DataFrame

In [7]:
# Prepare DataFrame for metrics
metrics = [
    'Annual Return',
    'Cumulative Returns',
    'Annual Volatility',
    'Sharpe Ratio',
    'Sortino Ratio']

columns = ['Backtest']

# Initialize the DataFrame with index set to evaluation metrics and column as `Backtest` (just like PyFolio)
portfolio_evaluation_df = pd.DataFrame(index=metrics, columns=columns)
portfolio_evaluation_df

Backtest
Annual Return           NaN
Cumulative Returns      NaN
Annual Volatility       NaN
Sharpe Ratio            NaN
Sortino Ratio           NaN

### Calculate and Assign Portfolio Evaluation Metrics

In [8]:
# Calculate cumulative return
# YOUR CODE HERE
portfolio_evaluation_df.loc['Cumulative Returns'] = signals_df['Portfolio Cumulative Returns'][-1]
# Calculate annualized return
# YOUR CODE HERE
portfolio_evaluation_df.loc['Annual Return'] = (
    signals_df['Portfolio Daily Returns'].mean() * 252
)
# Calculate annual volatility
# YOUR CODE HERE
portfolio_evaluation_df.loc['Annual Volatility'] = (
    signals_df['Portfolio Daily Returns'].std() * np.sqrt(252)
)
# Calculate Sharpe Ratio
# YOUR CODE HERE
portfolio_evaluation_df.loc['Sharpe Ratio'] = (
    signals_df['Portfolio Daily Returns'].mean() * 252) / (
    signals_df['Portfolio Daily Returns'].std() * np.sqrt(252)
)
# Calculate Downside Return
# YOUR CODE HERE
sortino_ratio_df = signals_df[['Portfolio Daily Returns']]

In [9]:
sortino_ratio_df.head()

Portfolio Daily Returns
Date                                       
5/25/2018 16:00:00                      NaN
5/29/2018 16:00:00                      NaN
5/30/2018 16:00:00                      0.0
5/31/2018 16:00:00                      0.0
6/1/2018 16:00:00                       0.0

In [13]:
sortino_ratio_df.loc[:,'Downside Returns'] = 0
sortino_ratio_df.head()

target = 0
mask = sortino_ratio_df['Portfolio Daily Returns'] < target
sortino_ratio_df.loc[mask, 'Downside Returns'] = sortino_ratio_df['Portfolio Daily Returns']**2

# Calculate Sortino Ratio
# YOUR CODE HERE
down_stdev = np.sqrt(sortino_ratio_df['Downside Returns'].mean()) * np.sqrt(252)
expected_return = sortino_ratio_df['Portfolio Daily Returns'].mean() * 252
sortino_ratio = expected_return/down_stdev

portfolio_evaluation_df.loc['Sortino Ratio'] = sortino_ratio
portfolio_evaluation_df.head()

Backtest
Annual Return       0.893477
Cumulative Returns   5.36895
Annual Volatility   0.626555
Sharpe Ratio         1.42602
Sortino Ratio        2.28521

In [11]:
# Initialize trade evaluation DataFrame with columns
trade_evaluation_df = pd.DataFrame(
    columns=[
        'Stock', 
        'Entry Date', 
        'Exit Date', 
        'Shares', 
        'Entry Share Price', 
        'Exit Share Price', 
        'Entry Portfolio Holding', 
        'Exit Portfolio Holding', 
        'Profit/Loss']
)

trade_evaluation_df

Empty DataFrame
Columns: [Stock, Entry Date, Exit Date, Shares, Entry Share Price, Exit Share Price, Entry Portfolio Holding, Exit Portfolio Holding, Profit/Loss]
Index: []

In [12]:
# Initialize iterative variables
entry_date = ''
exit_date = ''
entry_portfolio_holding = 0
exit_portfolio_holding = 0
share_size = 0
entry_share_price = 0
exit_share_price = 0

# Loop through signal DataFrame
# If `Entry/Exit` is 1, set entry trade metrics
# Else if `Entry/Exit` is -1, set exit trade metrics and calculate profit,
# Then append the record to the trade evaluation DataFrame
for index, row in signals_df.iterrows():
    if row['Entry/Exit'] == 1:
        entry_date = index
        entry_portfolio_holding = abs(row['Portfolio Holdings'])
        share_size = row['Entry/Exit Position']
        entry_share_price = row['Close']

    elif row['Entry/Exit'] == -1:
        exit_date = index
        exit_portfolio_holding = abs(row['Close'] * row['Entry/Exit Position'])
        exit_share_price = row['Close']
        profit_loss =  exit_portfolio_holding - entry_portfolio_holding
        trade_evaluation_df = trade_evaluation_df.append(
            {
                'Stock': 'ROKU',
                'Entry Date': entry_date,
                'Exit Date': exit_date,
                'Shares': share_size,
                'Entry Share Price': entry_share_price,
                'Exit Share Price': exit_share_price,
                'Entry Portfolio Holding': entry_portfolio_holding,
                'Exit Portfolio Holding': exit_portfolio_holding,
                'Profit/Loss': profit_loss
            },
            ignore_index=True)

# Print the DataFrame
trade_evaluation_df

Stock         Entry Date            Exit Date  Shares  Entry Share Price  \
0  ROKU  8/7/2018 16:00:00  11/29/2018 16:00:00   150.0              47.42   
1  ROKU  3/6/2019 16:00:00   2/19/2020 16:00:00   150.0              71.89   

   Exit Share Price  Entry Portfolio Holding  Exit Portfolio Holding  \
0             40.84                   7113.0                  6126.0   
1            126.56                  10783.5                 18984.0   

   Profit/Loss  
0       -987.0  
1       8200.5